In [26]:
import requests
import pandas as pd
import numpy as np

http_proxy  = "http://proxy-web.micron.com:80"
https_proxy = "http://proxy-web.micron.com:80"
proxyDict = { 
    "http":http_proxy, 
    "https":https_proxy              
}

pd.set_option('display.max_rows', None) #show every row for pandas
pd.set_option('display.max_columns', None) #show every column for pandas

In [27]:
# sii:上市, otc:上櫃
# TWSE之數據是至該季的累計數據而非單季數據, EX: Q3=> TWSE: Q1~Q3, 財報狗:Q3
def financial_statement(year, season, stocktype, type='綜合損益彙總表'):
    if year >= 1000:
        year -= 1911
        
    if type == '綜合損益彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb04'
    elif type == '資產負債彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb05'
    elif type == '營益分析彙總表':
        url = 'http://mops.twse.com.tw/mops/web/ajax_t163sb06'
    else:
        print('type does not match')
    
    r = requests.post(url, {
        'encodeURIComponent':1,
        'step':1,
        'firstin':1,
        'off':1,
        'TYPEK':stocktype,
        'year':str(year),
        'season':str(season),
    }, stream=True, verify=False, proxies=proxyDict)
    
    r.encoding = 'utf8'
    dfs = pd.read_html(r.text)
    
    
    for i, df in enumerate(dfs):
        df.columns = df.iloc[0]
        dfs[i] = df.iloc[1:]
        
    df = pd.concat(dfs).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['公司代號'] != '公司代號']
    df = df[~df['公司代號'].isnull()]
    
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_suffix.html
    #http://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.add_prefix.html
    suffix_format = "_{0}Q{1}".format(year, season)
    
    #return df.add_suffix(suffix_format)
    return df

In [28]:
def generate_df_for_stocktype(year, season, howmany_year_data, stocktype, title_name, with_col_name, sheettype):
    df = financial_statement(year, season, stocktype, type=sheettype)[['公司代號','公司名稱',with_col_name]]
    df.rename(columns = {df.columns[2]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

    for i in range(howmany_year_data*4):
        # calculate previous quarter data 107Q1 => we want the previous data is 106Q4 AND then 106Q3, 106Q2, 106Q1, 105Q4
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        #https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.merge.html
        dfanother = financial_statement(year, season, stocktype, type=sheettype)[['公司代號',with_col_name]]    
        print(dfanother.columns[1])

        dfanother.rename(columns = {dfanother.columns[1]: '{0}(%)_{1}Q{2}'.format(title_name, year, season)}, inplace = True)

        df = df.merge(dfanother, on='公司代號', how='inner')
        print("year:", year)
        #print("year: {0}".format(year))
        print("season:", season)
        #print("season: {0}".format(season))

    return df

In [29]:
df_eps_sii = generate_df_for_stocktype(107, 1, 3, 'sii', 'EPS', '基本每股盈餘（元）', '綜合損益彙總表')

df_eps_sii

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



基本每股盈餘（元）
year: 106
season: 4
基本每股盈餘（元）
year: 106
season: 3
基本每股盈餘（元）
year: 106
season: 2
基本每股盈餘（元）
year: 106
season: 1
基本每股盈餘（元）
year: 105
season: 4
基本每股盈餘（元）
year: 105
season: 3
基本每股盈餘（元）
year: 105
season: 2
基本每股盈餘（元）
year: 105
season: 1
基本每股盈餘（元）
year: 104
season: 4
基本每股盈餘（元）
year: 104
season: 3
基本每股盈餘（元）
year: 104
season: 2
基本每股盈餘（元）
year: 104
season: 1


公司代號     公司名稱 EPS(%)_107Q1 EPS(%)_106Q4 EPS(%)_106Q3 EPS(%)_106Q2  \
0    2801     彰化銀行         0.36         1.28         0.99         0.63   
1    2809     京城銀行         1.13         4.89         3.74         2.40   
2    2812     台中銀行         0.27         1.10         0.80         0.51   
3    2820       華票         0.25         1.01         0.76         0.49   
4    2834     臺灣企銀         0.30         0.82         0.76         0.51   
5    2836       高銀         0.01         0.47         0.56         0.39   
6    2838     聯邦銀行         0.26         1.05         0.78         0.49   
7    2845     遠東商銀         0.23         0.90         0.78         0.53   
8    2849     安泰銀行         0.26         1.24         0.96         0.60   
9    2855     統一證券         0.08         1.88         1.28         0.80   
10   2856     元富證券         0.24         0.60         0.45         0.27   
11   6005      群益證         0.37         1.33         0.90         0.49   
12   6024      群益期         2.57         4.68         3.67         2.02   
13   1101       台泥         0.69         2.03         1.34         0.81   
14   1102       亞泥         0.60         1.74         1.20         0.59   
15   1103       嘉泥         0.24         1.39        -0.07        -0.16   
16   1104     環球水泥         0.01         2.16         1.57         1.04   
17   1108     幸福水泥        -0.01        -0.25         0.05         0.07   
18   1109     信大水泥         0.34         1.32         0.72         0.42   
19   1110       東泥         0.03         0.11         0.01        -0.01   
20   1201     味全公司         0.23         1.31         0.17         0.10   
21   1203     味王公司         0.31         1.86         1.49         0.85   
22   1210     大成長城         1.16         3.28         2.24         1.29   
23   1213       大飲         0.03         0.04         0.21        -0.01   
24   1215     卜蜂企業         0.98         5.35         3.90         2.71   
25   1216       統一         0.75         7.01         2.62         1.61   
26   1217      愛之味         0.08         0.27         0.00        -0.12   
27   1218     泰山企業         0.19         0.93         0.88        -0.01   
28   1219     福壽實業         0.15         0.44         0.19         0.10   
29   1220       台榮         0.18         0.44         0.38         0.18   
30   1225      福懋油         0.38         1.13         1.11         0.70   
31   1227       佳格         0.82         2.39         1.66         0.92   
32   1229     聯華實業         0.57         3.11         2.40         1.18   
33   1231     聯華食品         0.84         2.54         1.72         0.93   
34   1232      大統益         1.23         5.11         3.79         2.32   
35   1233       天仁         0.43         1.94         1.48         0.94   
36   1234       黑松         0.30         1.35         1.13         0.40   
37   1235       興泰         0.15         5.23         5.15         1.76   
38   1236     宏亞食品         0.31         0.05        -0.24        -0.37   
39   1256  鮮活果汁-KY         2.13        10.01         9.26         5.11   
40   1262    綠悅-KY        -0.14         4.69         4.64         4.10   
41   1301       台塑         1.87         7.76         5.74         3.08   
42   1303     南亞塑膠         1.70         6.87         4.61         2.51   
43   1304       台聚         0.24         1.06         0.84         0.50   
44   1305       華夏         1.10         2.58         1.84         1.28   
45   1307     三芳化工         0.26         2.27         1.99         1.47   
46   1308       亞聚         0.16         1.09         0.92         0.63   
47   1309     台達化工         0.58         1.53         0.79         0.08   
48   1310       台苯         0.75         2.00         1.73         1.02   
49   1312     國喬石化         1.08         3.64         2.44         1.08   
50   1313       聯成         0.37         2.02         1.57         0.48   
51   1314      中石化         0.41         2.55         2.11         1.85   
52   1315     達新工業        -0.04         0.90         1.02         0.03   
53   1316

In [31]:
df_eps_otc = generate_df_for_stocktype(107, 1, 3, 'otc', 'EPS', '基本每股盈餘（元）', '綜合損益彙總表')

df_eps_otc

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:34: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.



基本每股盈餘（元）
year: 106
season: 4
基本每股盈餘（元）
year: 106
season: 3
基本每股盈餘（元）
year: 106
season: 2
基本每股盈餘（元）
year: 106
season: 1
基本每股盈餘（元）
year: 105
season: 4
基本每股盈餘（元）
year: 105
season: 3
基本每股盈餘（元）
year: 105
season: 2
基本每股盈餘（元）
year: 105
season: 1
基本每股盈餘（元）
year: 104
season: 4
基本每股盈餘（元）
year: 104
season: 3
基本每股盈餘（元）
year: 104
season: 2
基本每股盈餘（元）
year: 104
season: 1


公司代號    公司名稱 EPS(%)_107Q1 EPS(%)_106Q4 EPS(%)_106Q3 EPS(%)_106Q2  \
0    6015    宏遠證券        -0.08         0.57         0.51         0.10   
1    6016    康和證券        -0.26         1.15         0.76         0.13   
2    6020     大展證        -0.03         0.95         0.86         0.38   
3    6021     大慶證         0.13         0.55         0.47         0.29   
4    6023    元大期貨         0.89         3.76         2.64         1.48   
5    6026    福邦證券         0.34         2.00         1.52         0.99   
6    1258   其祥-KY         0.17         1.26         1.46         1.25   
7    1259      安心         0.80         5.23         4.50         2.73   
8    1264      德麥         2.85        13.41        10.02         6.60   
9    1333     恩得利        -0.91        -1.93        -1.47        -0.89   
10   1336      台翰         0.14         1.44         1.13         0.67   
11   1565    精華光學         7.00        31.52        23.68        13.82   
12   1566      捷邦         0.05         1.03         0.69         0.33   
13   1569      濱川         0.03         2.61         1.91         1.25   
14   1570    力肯實業         0.19         1.48         1.28         0.54   
15   1580    新麥企業         0.98        11.01         7.92         4.23   
16   1584    精剛精密        -0.40        -0.96        -0.57        -0.45   
17   1586    和勤精機         0.20         0.42         0.25         0.03   
18   1591   駿吉-KY         0.01         0.06         0.09         0.10   
19   1593      祺驊         0.31         3.77         2.61         1.15   
20   1595    川寶科技         0.34         7.12         2.43         1.79   
21   1597      直得         1.69         4.03         2.60         1.23   
22   1599     宏佳騰        -0.19         2.40         1.29         0.72   
23   1742      台蠟        -0.34         0.12         0.07         0.05   
24   1752      南光         0.37         1.84         1.33         1.00   
25   1777      生泰         0.86         1.99         1.52         1.19   
26   1781    合世生醫        -0.36        -1.44        -1.04        -0.86   
27   1784    訊聯生技         0.19        -0.13        -0.15        -0.09   
28   1785     光洋科         0.34         0.33         0.16         0.11   
29   1787     福盈科         0.34         1.98         1.49         0.96   
30   1788    杏昌生技         1.70         7.17         5.09         3.53   
31   1795    美時製藥         0.07         0.03         0.05        -0.16   
32   1799      易威        -0.54        -3.50        -2.62        -1.71   
33   1813     寶利徠         0.18         0.05         0.25         0.18   
34   1815    富喬工業         0.34         1.16         1.16         0.68   
35   2035    唐榮公司        -0.47         0.69         0.78         0.75   
36   2061      風青         0.14         0.50         0.32         0.11   
37   2063      世鎧         0.82         2.63         2.04         1.16   
38   2064      晉椿         0.01         0.41         0.28         0.07   
39   2066      世德         0.27         4.67         3.54         1.98   
40   2067      嘉鋼         0.10        -1.38        -1.41        -1.53   
41   2221    大甲永和         0.66         2.06         1.37         0.80   
42   2230      泰茂        -0.24        -0.44        -0.44        -0.33   
43   2233      宇隆         1.54         8.05         5.91         3.63   
44   2235      謚源         0.55         3.48         3.15         2.23   
45   2596    綠意開發         2.18         2.72         1.24         0.89   
46   2640     大車隊         1.33         4.56         3.52         2.54   
47   2641    正德海運         0.14        -2.76        -0.02        -0.06   
48   2718      晶悅        -0.03         0.10        -0.05        -0.06   
49   2719     燦星旅        -1.11        -3.31        -2.67        -1.56   
50   2724   富驛-KY        -0.68        -4.05        -2.49        -2.22   
51   2726   雅茗-KY         1.05         5.02         4.23         2.67   
52   2729    瓦城泰統         3.95        14.12        11.58         7.44   
53   2732    六角國際         0.42         5.02         3.60       

In [32]:
#Database-style DataFrame joining/merging: join, merge
#Concatenating objects: concat, append

#ignore_index = True 可以忽略合併時舊的 index 欄位，改採用自動產生的 index
df_eps = pd.concat([df_eps_sii,df_eps_otc],axis=0, ignore_index=True)

df_eps

公司代號     公司名稱 EPS(%)_107Q1 EPS(%)_106Q4 EPS(%)_106Q3 EPS(%)_106Q2  \
0     2801     彰化銀行         0.36         1.28         0.99         0.63   
1     2809     京城銀行         1.13         4.89         3.74         2.40   
2     2812     台中銀行         0.27         1.10         0.80         0.51   
3     2820       華票         0.25         1.01         0.76         0.49   
4     2834     臺灣企銀         0.30         0.82         0.76         0.51   
5     2836       高銀         0.01         0.47         0.56         0.39   
6     2838     聯邦銀行         0.26         1.05         0.78         0.49   
7     2845     遠東商銀         0.23         0.90         0.78         0.53   
8     2849     安泰銀行         0.26         1.24         0.96         0.60   
9     2855     統一證券         0.08         1.88         1.28         0.80   
10    2856     元富證券         0.24         0.60         0.45         0.27   
11    6005      群益證         0.37         1.33         0.90         0.49   
12    6024      群益期         2.57         4.68         3.67         2.02   
13    1101       台泥         0.69         2.03         1.34         0.81   
14    1102       亞泥         0.60         1.74         1.20         0.59   
15    1103       嘉泥         0.24         1.39        -0.07        -0.16   
16    1104     環球水泥         0.01         2.16         1.57         1.04   
17    1108     幸福水泥        -0.01        -0.25         0.05         0.07   
18    1109     信大水泥         0.34         1.32         0.72         0.42   
19    1110       東泥         0.03         0.11         0.01        -0.01   
20    1201     味全公司         0.23         1.31         0.17         0.10   
21    1203     味王公司         0.31         1.86         1.49         0.85   
22    1210     大成長城         1.16         3.28         2.24         1.29   
23    1213       大飲         0.03         0.04         0.21        -0.01   
24    1215     卜蜂企業         0.98         5.35         3.90         2.71   
25    1216       統一         0.75         7.01         2.62         1.61   
26    1217      愛之味         0.08         0.27         0.00        -0.12   
27    1218     泰山企業         0.19         0.93         0.88        -0.01   
28    1219     福壽實業         0.15         0.44         0.19         0.10   
29    1220       台榮         0.18         0.44         0.38         0.18   
30    1225      福懋油         0.38         1.13         1.11         0.70   
31    1227       佳格         0.82         2.39         1.66         0.92   
32    1229     聯華實業         0.57         3.11         2.40         1.18   
33    1231     聯華食品         0.84         2.54         1.72         0.93   
34    1232      大統益         1.23         5.11         3.79         2.32   
35    1233       天仁         0.43         1.94         1.48         0.94   
36    1234       黑松         0.30         1.35         1.13         0.40   
37    1235       興泰         0.15         5.23         5.15         1.76   
38    1236     宏亞食品         0.31         0.05        -0.24        -0.37   
39    1256  鮮活果汁-KY         2.13        10.01         9.26         5.11   
40    1262    綠悅-KY        -0.14         4.69         4.64         4.10   
41    1301       台塑         1.87         7.76         5.74         3.08   
42    1303     南亞塑膠         1.70         6.87         4.61         2.51   
43    1304       台聚         0.24         1.06         0.84         0.50   
44    1305       華夏         1.10         2.58         1.84         1.28   
45    1307     三芳化工         0.26         2.27         1.99         1.47   
46    1308       亞聚         0.16         1.09         0.92         0.63   
47    1309     台達化工         0.58         1.53         0.79         0.08   
48    1310       台苯         0.75         2.00         1.73         1.02   
49    1312     國喬石化         1.08         3.64         2.44         1.08   
50    1313       聯成         0.37         2.02         1.57         0.48   
51    1314      中石化         0.41         2.55         2.11         1.85   
52    1315     達新工業        -0.0

In [33]:
#檢查column資料型態

#df_eps.info() #non-null object
#df_eps.dtypes #object
#df_eps.applymap(np.isreal) #all False
'''
公司代號              int64
公司名稱             object
EPS(%)_107Q1    float64
EPS(%)_106Q4    float64
EPS(%)_106Q3    float64
EPS(%)_106Q2    float64
EPS(%)_106Q1    float64
EPS(%)_105Q4    float64
EPS(%)_105Q3    float64
EPS(%)_105Q2    float64
EPS(%)_105Q1    float64
EPS(%)_104Q4    float64
EPS(%)_104Q3    float64
EPS(%)_104Q2    float64
EPS(%)_104Q1    float64
dtype: object
'''

df_eps = df_eps.convert_objects(convert_numeric=True) #轉成float型態方便後續處理

df_eps.convert_objects(convert_numeric=True).dtypes #轉成float型態方便後續處理

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:25: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:27: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.


公司代號              int64
公司名稱             object
EPS(%)_107Q1    float64
EPS(%)_106Q4    float64
EPS(%)_106Q3    float64
EPS(%)_106Q2    float64
EPS(%)_106Q1    float64
EPS(%)_105Q4    float64
EPS(%)_105Q3    float64
EPS(%)_105Q2    float64
EPS(%)_105Q1    float64
EPS(%)_104Q4    float64
EPS(%)_104Q3    float64
EPS(%)_104Q2    float64
EPS(%)_104Q1    float64
dtype: object

In [34]:
def isFloat(element):  
    try:
        float(element)
        return True
    except ValueError:
        return False

In [35]:
def growth_func(row, year, season):
    previous_year = year - 1
    #判斷是否為文字而非數字
    if(isFloat(row['EPS(%)_{0}Q{1}'.format(year, season)]) == True):
        subsequent_value = float(row['EPS(%)_{0}Q{1}'.format(year, season)])
        previous_value = float(row['EPS(%)_{0}Q{1}'.format(previous_year, season)])
   
        if(previous_value == 0):
            result = ((subsequent_value - previous_value)/np.abs(subsequent_value))*100
        else:
            result = ((subsequent_value - previous_value)/np.abs(previous_value))*100            
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
     
    else:
        return 'NoValue'

In [36]:
def ma2q_growth_func(row, year, season):
    #判斷是否為文字而非數字
    if(isFloat(row['EPS(%)_{0}Q{1}'.format(year, season)]) == True):
        previous_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        if (season != 1):
            season = season - 1
        else:
            season = 4
            year = year - 1
        subsequent_value = float(row['Growth_{0}Q{1}'.format(year, season)])
        
        result = ((subsequent_value + previous_value)/2)
        return float("{0:.2f}".format(result)) # Limiting floats to two decimal points
    
    else:
        return 'NoValue'

In [37]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4)):
    df_eps['Growth_{0}Q{1}'.format(year, season)] = df_eps.apply (lambda row: growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [38]:
# use the apply function in pandas to apply the function
# Note the axis=1 specifier, that means that the application is done at a row, rather than a column level
# df_eps.apply (lambda row: growth_func (row),axis=1)

year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
for i in range(int(howmany_year_data*4-4-1)):
    df_eps['2QMAGrowth_{0}Q{1}'.format(year, season)] = df_eps.apply (lambda row: ma2q_growth_func(row, year, season),axis=1)
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

In [39]:
# pandas styling
def color_white(val):
    """
    Takes a scalar and returns a string with
    the css property `'color: red'` for negative
    strings, black otherwise.
    """
    color = 'white'
    return 'color: %s' % color

def background_color(val):    
    if float(val) < 0:
        backgroundcolor = '#ff0000'
    elif float(val) < 10:
        backgroundcolor = '#f47721'
    elif float(val) < 20:
        backgroundcolor = '#ffdd00'
    elif float(val) < 30:
        backgroundcolor = '#5ecc62'
    else:
        backgroundcolor = '#00ad45'
    return 'background-color: %s' % backgroundcolor

In [40]:
def get_basic_info_for_ftock(stocktype):

    #get basic info of company
    '''
    抓取上市櫃股票的代號、名稱...等資料。
    上市
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=2
    上櫃
    http://isin.twse.com.tw/isin/C_public.jsp?strMode=4
    '''
    #http://bloggerkaiweng.blogspot.com/2016/09/python.html

    if(stocktype == 'sii'):
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=2'
    else:
        url='http://isin.twse.com.tw/isin/C_public.jsp?strMode=4'
    
    r = requests.get(url, stream=True, verify=False, proxies=proxyDict)
    r.encoding = 'big5hkscs' 
    dfshow = pd.read_html(r.text)

    for i, df in enumerate(dfshow):
        df.columns = df.iloc[0]
        dfshow[i] = df.iloc[1:]

    df = pd.concat(dfshow).applymap(lambda x: x if x != '--' else np.nan)
    df = df[df['有價證券代號及名稱'] != '股票']
    df = df[~df['有價證券代號及名稱'].isnull()]
    df = df.reset_index(drop=True)
    
    newdf=df[df['產業別'] > '0']
    del newdf['國際證券辨識號碼(ISIN Code)'],newdf['CFICode'],newdf['備註']

    df2=newdf['有價證券代號及名稱'].str.split(' ', expand=True)
    df2 = df2.reset_index(drop=True)
    newdf = newdf.reset_index(drop=True)
    for i in df2.index:
        if '　' in df2.iat[i,0]:
            df2.iat[i,1]=df2.iat[i,0].split('　')[1]
            df2.iat[i,0]=df2.iat[i,0].split('　')[0]
    newdf=df2.join(newdf)
    newdf=newdf.rename(columns = {0:'公司代號',1:'股票名稱'})
    del newdf['有價證券代號及名稱']

    return newdf

In [41]:
df_basicinfo_sii = get_basic_info_for_ftock('sii').convert_objects(convert_numeric=True) #轉成float型態
df_basicinfo_otc = get_basic_info_for_ftock('otc').convert_objects(convert_numeric=True) #轉成float型態

df_basicinfo = pd.concat([df_basicinfo_sii,df_basicinfo_otc],axis=0, ignore_index=True)
#df_eps_basicinfo_sii.dtypes
#df_eps_basicinfo_otc

df_eps = df_eps.merge(df_basicinfo, on='公司代號', how='inner')

df_eps

C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  """Entry point for launching an IPython kernel.
C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\ipykernel_launcher.py:2: FutureWarning: convert_objects is deprecated.  To re-infer data dtypes for object columns, use DataFrame.infer_objects()
For all other conversions use the data-type specific converters pd.to_datetime, pd.to_timedelta and pd.to_numeric.
  


公司代號     公司名稱  EPS(%)_107Q1  EPS(%)_106Q4  EPS(%)_106Q3  EPS(%)_106Q2  \
0     2801     彰化銀行          0.36          1.28          0.99          0.63   
1     2809     京城銀行          1.13          4.89          3.74          2.40   
2     2812     台中銀行          0.27          1.10          0.80          0.51   
3     2820       華票          0.25          1.01          0.76          0.49   
4     2834     臺灣企銀          0.30          0.82          0.76          0.51   
5     2836       高銀          0.01          0.47          0.56          0.39   
6     2838     聯邦銀行          0.26          1.05          0.78          0.49   
7     2845     遠東商銀          0.23          0.90          0.78          0.53   
8     2849     安泰銀行          0.26          1.24          0.96          0.60   
9     2855     統一證券          0.08          1.88          1.28          0.80   
10    2856     元富證券          0.24          0.60          0.45          0.27   
11    6005      群益證          0.37          1.33          0.90          0.49   
12    6024      群益期          2.57          4.68          3.67          2.02   
13    1101       台泥          0.69          2.03          1.34          0.81   
14    1102       亞泥          0.60          1.74          1.20          0.59   
15    1103       嘉泥          0.24          1.39         -0.07         -0.16   
16    1104     環球水泥          0.01          2.16          1.57          1.04   
17    1108     幸福水泥         -0.01         -0.25          0.05          0.07   
18    1109     信大水泥          0.34          1.32          0.72          0.42   
19    1110       東泥          0.03          0.11          0.01         -0.01   
20    1201     味全公司          0.23          1.31          0.17          0.10   
21    1203     味王公司          0.31          1.86          1.49          0.85   
22    1210     大成長城          1.16          3.28          2.24          1.29   
23    1213       大飲          0.03          0.04          0.21         -0.01   
24    1215     卜蜂企業          0.98          5.35          3.90          2.71   
25    1216       統一          0.75          7.01          2.62          1.61   
26    1217      愛之味          0.08          0.27          0.00         -0.12   
27    1218     泰山企業          0.19          0.93          0.88         -0.01   
28    1219     福壽實業          0.15          0.44          0.19          0.10   
29    1220       台榮          0.18          0.44          0.38          0.18   
30    1225      福懋油          0.38          1.13          1.11          0.70   
31    1227       佳格          0.82          2.39          1.66          0.92   
32    1229     聯華實業          0.57          3.11          2.40          1.18   
33    1231     聯華食品          0.84          2.54          1.72          0.93   
34    1232      大統益          1.23          5.11          3.79          2.32   
35    1233       天仁          0.43          1.94          1.48          0.94   
36    1234       黑松          0.30          1.35          1.13          0.40   
37    1235       興泰          0.15          5.23          5.15          1.76   
38    1236     宏亞食品          0.31          0.05         -0.24         -0.37   
39    1256  鮮活果汁-KY          2.13         10.01          9.26          5.11   
40    1262    綠悅-KY         -0.14          4.69          4.64          4.10   
41    1301       台塑          1.87          7.76          5.74          3.08   
42    1303     南亞塑膠          1.70          6.87          4.61          2.51   
43    1304       台聚          0.24          1.06          0.84          0.50   
44    1305       華夏          1.10          2.58          1.84          1.28   
45    1307     三芳化工          0.26          2.27          1.99          1.47   
46    1308       亞聚          0.16          1.09          0.92          0.63   
47    1309     台達化工          0.58          1.53          0.79          0.08   
48    1310       台苯          0.75          2.00          1.73          1.02   
49    1312     國喬石化          1.08          3.64         

In [42]:
# styled dataframe can use .to_excel('Styled_Basic_EPS.xlsx', engine='openpyxl') to export excel with style
year = 107
season = 1
howmany_year_data = 3

#first 4 quarter don't need to be calculated growth
columns_name = []
for i in range(int(howmany_year_data*4-4)):
    columns_name.append('Growth_{0}Q{1}'.format(year, season))
    columns_name.append('2QMAGrowth_{0}Q{1}'.format(year, season))
    if (season != 1):
        season = season - 1
    else:
        season = 4
        year = year - 1

print(columns_name)
# the cell’s style depends only on it’s own value. That means we should use the Styler.applymap method which works elementwise.
# Now suppose you wanted to highlight the maximum value in each column. We can’t use .applymap anymore since that operated elementwise. Instead, we’ll turn to .apply which operates columnwise (or rowwise using the axis keyword).
#df_eps.style.applymap(color_negative_red, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).applymap(background_color, subset=pd.IndexSlice[:, ['Growth_107Q1','Growth_106Q4','Growth_106Q3','Growth_106Q2','Growth_106Q1','Growth_105Q4','Growth_105Q3','Growth_105Q2']]).to_excel('Styled_Basic_EPS.xlsx', 'EPS_Basic', engine='openpyxl')
df_eps.style.applymap(color_white, subset=pd.IndexSlice[:, columns_name]).applymap(background_color, subset=pd.IndexSlice[:, columns_name]).to_excel('Styled_Basic_Perspective_EPS.xlsx', 'EPS_Basic', engine='openpyxl')

# Pandas style function to hignlight specific columns
# http://pandas.pydata.org/pandas-docs/stable/style.html#Finer-Control:-Slicing
# Finer Control: Slicing
# ex: df.style.apply(highlight_max, subset=['B', 'C', 'D'])

['Growth_107Q1', '2QMAGrowth_107Q1', 'Growth_106Q4', '2QMAGrowth_106Q4', 'Growth_106Q3', '2QMAGrowth_106Q3', 'Growth_106Q2', '2QMAGrowth_106Q2', 'Growth_106Q1', '2QMAGrowth_106Q1', 'Growth_105Q4', '2QMAGrowth_105Q4', 'Growth_105Q3', '2QMAGrowth_105Q3', 'Growth_105Q2', '2QMAGrowth_105Q2']


C:\Users\terrencechen\AppData\Local\conda\conda\envs\python35\lib\site-packages\pandas\core\indexing.py:1472: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/indexing.html#deprecate-loc-reindex-listlike
  return self._getitem_tuple(key)
